# Embedding models

In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-MiniLM-L6-v2')
model

SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [3]:
tokenized_data = model.tokenize(["walker walked a long walk"])
tokenized_data


{'input_ids': tensor([[ 101, 5232, 2939, 1037, 2146, 3328,  102]]),
 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0]]),
 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1]])}

In [4]:
first_module = model._first_module()
first_module.auto_model

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 384, padding_idx=0)
    (position_embeddings): Embedding(512, 384)
    (token_type_embeddings): Embedding(2, 384)
    (LayerNorm): LayerNorm((384,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-5): 6 x BertLayer(
        (attention): BertAttention(
          (self): BertSdpaSelfAttention(
            (query): Linear(in_features=384, out_features=384, bias=True)
            (key): Linear(in_features=384, out_features=384, bias=True)
            (value): Linear(in_features=384, out_features=384, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=384, out_features=384, bias=True)
            (LayerNorm): LayerNorm((384,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False)


In [5]:
embeddings = first_module.auto_model.embeddings
embeddings

BertEmbeddings(
  (word_embeddings): Embedding(30522, 384, padding_idx=0)
  (position_embeddings): Embedding(512, 384)
  (token_type_embeddings): Embedding(2, 384)
  (LayerNorm): LayerNorm((384,), eps=1e-12, elementwise_affine=True)
  (dropout): Dropout(p=0.1, inplace=False)
)

## No context aware embeddings

In [6]:
import torch
import plotly.express as px

device = torch.device('mps' if torch.backends.mps.is_available() else 'cpu')
device = 'mps'


first_sentence = "vector search optimization"
second_sentence = "we learn about vector search optimization"

with torch.no_grad():
    first_tokens = model.tokenize([first_sentence])
    second_tokens = model.tokenize([second_sentence])

     # Convert the input_ids tensors to the device
    first_embedding = embeddings.word_embeddings(first_tokens['input_ids'].to(device))
    second_embedding = embeddings.word_embeddings(second_tokens['input_ids'].to(device))


first_embedding.shape, second_embedding.shape



(torch.Size([1, 5, 384]), torch.Size([1, 8, 384]))

In [12]:
from sentence_transformers import util



distances= util.cos_sim(first_embedding.squeeze(), second_embedding.squeeze()).cpu().numpy()
distances = distances.T
px.imshow(
    distances,
    x=model.tokenizer.convert_ids_to_tokens(
        first_tokens['input_ids'][0]
        ),
    y=model.tokenizer.convert_ids_to_tokens(
        second_tokens['input_ids'][0]
        ),
    text_auto=True,
)


In [13]:
token_embeddings = first_module.auto_model \
                    .embeddings \
                    .word_embeddings \
                    .weight \
                    .detach() \
                    .cpu() \
                    .numpy()

token_embeddings.shape

(30522, 384)

In [14]:
import random

vocabulary = first_module.tokenizer.get_vocab()
sorted_vocabulary = sorted(
    vocabulary.items(),
    key=lambda x: x[1]
)

sorted_tokens = [token for token, _ in sorted_vocabulary]
random.choices(sorted_tokens, k=100)


['whorls',
 'teachings',
 'blond',
 '[unused421]',
 'tempered',
 '##oed',
 'series',
 'mickey',
 'periodical',
 'outstanding',
 'inflicted',
 'offs',
 'flying',
 'embracing',
 'growling',
 'majors',
 'adolescents',
 'geological',
 'huddled',
 'safer',
 'attributes',
 '‡',
 'societal',
 'politically',
 'vigor',
 'offenses',
 'depart',
 'documentation',
 'cello',
 '##dora',
 'overdose',
 'pagoda',
 'draper',
 'translations',
 '[unused236]',
 'aspect',
 'affairs',
 'fathers',
 '276',
 '##riding',
 'automated',
 'leukemia',
 'troll',
 'creeks',
 'imminent',
 'hated',
 'founders',
 'residency',
 '##ː',
 '##economic',
 '1920',
 'hostile',
 'francesco',
 'robbins',
 'downloaded',
 'francais',
 'accepting',
 '##app',
 'twinkle',
 'satisfy',
 '##⁴',
 'myanmar',
 'irony',
 'adjustments',
 'flanders',
 'solved',
 'eireann',
 'doncaster',
 '##olio',
 'promotes',
 'distal',
 '##ी',
 'nixon',
 '##igh',
 'straw',
 'bradley',
 'eel',
 'thirty',
 '和',
 'cia',
 'lovely',
 'enroll',
 '##erate',
 'landmar

In [15]:
from sklearn.manifold import TSNE

tsne = TSNE(n_components=2, random_state=42, metric='cosine')
tsne_embeddings_2d = tsne.fit_transform(token_embeddings)
tsne_embeddings_2d.shape


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


(30522, 2)

In [16]:
token_colors = []

for token in sorted_tokens:
    if token[0] == "[" and token[-1] == "]":
        token_colors.append("red")
    elif token.startswith("##"):
        token_colors.append("blue")
    else:
        token_colors.append("green")


In [18]:
import plotly.graph_objs as go

scatter = go.Scatter(
    x=tsne_embeddings_2d[:, 0],
    y=tsne_embeddings_2d[:, 1],
    text=sorted_tokens,
    mode="markers",
    marker=dict(
        color=token_colors,
        size=3,
    ),
)

fig = go.Figure(data=[scatter],
                layout=dict(
                    width=600,
                    height=900,
                    margin=dict(l=0, r=0,),
                )
)

fig.show()



## Context aware embeddings

In [19]:
device = torch.device('mps' if torch.backends.mps.is_available() else 'cpu')
device = 'mps'


first_sentence = "vector search optimization"
second_sentence = "we learn about vector search optimization"

with torch.no_grad():
    first_tokens = model.tokenize([first_sentence])
    second_tokens = model.tokenize([second_sentence])

    first_embedding = model.encode([first_sentence], output_value='token_embeddings')
    second_embedding = model.encode([second_sentence], output_value='token_embeddings')

distances = util.cos_sim(first_embedding[0], second_embedding[0]).cpu().numpy()
distances = distances.T


In [20]:
px.imshow(
    distances,
    x=model.tokenizer.convert_ids_to_tokens(first_tokens['input_ids'][0]),
    y=model.tokenizer.convert_ids_to_tokens(second_tokens['input_ids'][0]),
    text_auto=True,
)

# Role of tokenizers

## BPE - Byte Pair Encoding

In [22]:
from tokenizers.trainers import BpeTrainer
from tokenizers.models import BPE
from tokenizers import Tokenizer
from tokenizers.pre_tokenizers import Whitespace

bpe_tokenizer = Tokenizer(BPE())
bpe_tokenizer.pre_tokenizer = Whitespace()

bpe_trainer = BpeTrainer(vocab_size=14)

In [23]:
training_data = ["walker walked a long walk"]

bpe_tokenizer.train_from_iterator(training_data, trainer=bpe_trainer)

In [24]:
bpe_tokenizer.get_vocab()

{'d': 1,
 'al': 10,
 'e': 2,
 'g': 3,
 'n': 6,
 'walk': 12,
 'wal': 11,
 'l': 5,
 'o': 7,
 'walke': 13,
 'k': 4,
 'r': 8,
 'w': 9,
 'a': 0}

In [26]:
bpe_tokenizer.encode("walker walked a long walk").tokens

['walke', 'r', 'walke', 'd', 'a', 'l', 'o', 'n', 'g', 'walk']

In [27]:
bpe_tokenizer.encode("wlk").tokens

['w', 'l', 'k']

In [28]:
bpe_tokenizer.encode("she walked").tokens

['e', 'walke', 'd']

## WordPiece

In [32]:
from real_wordpiece.trainer import RealWordPieceTrainer
from tokenizers.models import WordPiece

real_wordpiece_tokenizer = Tokenizer(WordPiece())
real_wordpiece_tokenizer.pre_tokenizer = Whitespace()

real_wordpiece_trainer = RealWordPieceTrainer(vocab_size=27)

In [33]:
real_wordpiece_trainer.train_tokenizer(
    training_data, real_wordpiece_tokenizer
)
real_wordpiece_tokenizer.get_vocab()

{'long': 21,
 '##ed': 23,
 '##lk': 25,
 'o': 16,
 'w': 0,
 'd': 15,
 'k': 12,
 '##l': 2,
 'lo': 19,
 'g': 18,
 '##ng': 20,
 '##k': 3,
 '##r': 7,
 'l': 6,
 '##o': 9,
 '##e': 4,
 '##a': 1,
 'e': 13,
 '##n': 10,
 '##er': 22,
 'walk': 26,
 'r': 14,
 'a': 5,
 '##d': 8,
 'wa': 24,
 'n': 17,
 '##g': 11}

In [34]:
real_wordpiece_tokenizer.encode("walker walked a long walk").tokens

['walk', '##er', 'walk', '##ed', 'a', 'long', 'walk']

In [35]:
real_wordpiece_tokenizer.encode("wlk").tokens

['w', '##lk']

## Huggingface wordpiece

In [37]:
from tokenizers.trainers import WordPieceTrainer

unk_token = "[UNK]"

wordpiece_model = WordPiece(unk_token=unk_token)
wordpiece_tokenizer = Tokenizer(wordpiece_model)
wordpiece_tokenizer.pre_tokenizer = Whitespace()
wordpiece_trainer = WordPieceTrainer(vocab_size=28, 
                                     special_tokens=[unk_token])

In [38]:
wordpiece_tokenizer.train_from_iterator(training_data,
                                        wordpiece_trainer)
wordpiece_tokenizer.get_vocab()

{'##n': 18,
 '##r': 15,
 'l': 6,
 '##a': 11,
 'wa': 20,
 'walk': 22,
 '##ng': 25,
 '[UNK]': 0,
 '##l': 12,
 '##k': 13,
 'e': 3,
 'k': 5,
 '##lk': 21,
 'g': 4,
 '##g': 19,
 '##d': 16,
 'walke': 23,
 'r': 9,
 'd': 2,
 'o': 8,
 'lo': 24,
 'walker': 26,
 'n': 7,
 'w': 10,
 '##e': 14,
 'a': 1,
 '##o': 17,
 'walked': 27}

In [39]:
wordpiece_tokenizer.encode("walker walked a long walk").tokens

['walker', 'walked', 'a', 'lo', '##ng', 'walk']

In [40]:
wordpiece_tokenizer.encode("wlk").tokens

['w', '##lk']

In [41]:
wordpiece_tokenizer.encode("she walked").tokens

['[UNK]', 'walked']

## Unigram

In [42]:
from tokenizers.trainers import UnigramTrainer
from tokenizers.models import Unigram

unigram_tokenizer = Tokenizer(Unigram())
unigram_tokenizer.pre_tokenizer = Whitespace()

unigram_trainer = UnigramTrainer(vocab_size=28, 
                                 special_tokens=[unk_token],
                                 unk_token=unk_token)
unigram_tokenizer.train_from_iterator(training_data, unigram_trainer)
unigram_tokenizer.get_vocab()

{'l': 6,
 '[UNK]': 0,
 'd': 8,
 'walk': 4,
 'r': 11,
 'a': 5,
 'w': 12,
 'walke': 1,
 'e': 2,
 'g': 10,
 'k': 3,
 'n': 9,
 'o': 7}

In [43]:
unigram_tokenizer.encode("walker walked a long walk").tokens

['walke', 'r', 'walke', 'd', 'a', 'l', 'o', 'n', 'g', 'walk']

In [44]:
unigram_tokenizer.encode("wlk").tokens


['w', 'l', 'k']

In [45]:
unigram_tokenizer.encode("she walked").tokens


['sh', 'e', 'walke', 'd']

In [46]:
unigram_tokenizer.encode("she walked").ids


[0, 2, 1, 8]

# Implication of Tokenization

# Measusring RAG

`Data from github repository:`https://github.com/wayfair/WANDS/blob/main/dataset/

In [1]:
import pandas as pd

products_df = pd.read_csv(
    f"product.csv", 
    sep="\t", 
    index_col="product_id", 
    keep_default_na=False,  # some products do not have a description
)
products_df.head()

product_name  \
product_id                                                      
0                                     solid wood platform bed   
1                                 all-clad 7 qt . slow cooker   
2                     all-clad electrics 6.5 qt . slow cooker   
3                all-clad all professional tools pizza cutter   
4           baldwin prestige alcott passage knob with roun...   

                           product_class  \
product_id                                 
0                                   Beds   
1                           Slow Cookers   
2                           Slow Cookers   
3           Slicers, Peelers And Graters   
4                             Door Knobs   

                                           category hierarchy  \
product_id                                                      
0           Furniture / Bedroom Furniture / Beds & Headboa...   
1           Kitchen & Tabletop / Small Kitchen Appliances ...   
2           Kitchen & Tabletop / Small Kitchen Appliances ...   
3                                  Browse By Brand / All-Clad   
4           Home Improvement / Doors & Door Hardware / Doo...   

                                          product_description  \
product_id                                                      
0           good , deep sleep can be quite difficult to ha...   
1           create delicious slow-cooked meals , from tend...   
2           prepare home-cooked meals on any schedule with...   
3           this original stainless tool was designed to c...   
4           the hardware has a rich heritage of delivering...   

                                             product_features rating_count  \
product_id                                                                   
0           overallwidth-sidetoside:64.7|dsprimaryproducts...         15.0   
1           capacityquarts:7|producttype : slow cooker|pro...        100.0   
2           features : keep warm setting|capacityquarts:6....        208.0   
3           overallwidth-sidetoside:3.5|warrantylength : l...         69.0   
4           compatibledoorthickness:1.375 '' |countryofori...         70.0   

           average_rating review_count  
product_id                              
0                     4.5         15.0  
1                     2.0         98.0  
2                     3.0        181.0  
3                     4.5         42.0  
4                     5.0         42.0

## Encode products name and description


In [2]:
from sentence_transformers import SentenceTransformer
num_products = 5000
model = SentenceTransformer("all-MiniLM-L6-v2")

product_name_embeddings = model.encode(
    products_df["product_name"][:num_products].tolist()
)
product_name_embeddings.shape

/opt/homebrew/Caskroom/miniconda/base/envs/llm/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange


(5000, 384)

In [3]:
product_description_embeddings = model.encode(
    products_df["product_description"][:num_products].tolist()
)
product_description_embeddings.shape

(5000, 384)

## Create empty collection in Qdrant

 `use docker to run qdrant`
 **docker run -p 6333:6333 qdrant/qdrant**


In [4]:
from qdrant_client import QdrantClient, models

client = QdrantClient("http://localhost:6333")
client.delete_collection("wands-products")
client.create_collection(
    collection_name="wands-products",
    vectors_config={
        "product_name": models.VectorParams(
            size=384,
            distance=models.Distance.COSINE,
        ),
        "product_description": models.VectorParams(
            size=384,
            distance=models.Distance.COSINE,
        ),
    },
    optimizers_config=models.OptimizersConfigDiff(
        default_segment_number=2,
        indexing_threshold=1000,
    ),
)

True

## Uploading data to Qdrant

In [5]:
client.upload_collection(
    collection_name="wands-products",
    vectors={
        "product_name": product_name_embeddings,
        "product_description": product_description_embeddings,
    },
    payload=products_df.to_dict(orient="records"),
    ids=products_df.index.tolist(),
    batch_size=64,
)


## Read queries and labels

In [6]:
queries_df = pd.read_csv(
    "query.csv", 
    sep="\t", 
    index_col="query_id",
)
queries_df.head()

query               query_class
query_id                                                     
0                       salon chair            Massage Chairs
1                smart coffee table  Coffee & Cocktail Tables
2                          dinosaur           Kids Wall Décor
3                 turquoise pillows            Accent Pillows
4         chair and a half recliner                 Recliners

In [7]:

labels_df = pd.read_csv(
    "label.csv", 
    sep="\t", 
)
labels_df.sample(n=5)

id  query_id  product_id       label
80363    80514       123       25616     Partial
23389    23389       151         483       Exact
10193    10193        80       32815     Partial
178388  178955       427       34861     Partial
155062  155629       384        2615  Irrelevant

## Create relevancy scores

In [8]:
relevancy_scores = {
    "Exact": 10,
    "Partial": 5,
    "Irrelevant": 0,
}

labels_df["score"] = labels_df["label"].map(relevancy_scores.get)
labels_df["query_id"] = labels_df["query_id"].map(lambda x: f"query_{x}")
labels_df["product_id"] = labels_df["product_id"].map(lambda x: f"doc_{x}")
labels_df.sample(n=5)

id   query_id product_id       label  score
182934  183501  query_434  doc_22693  Irrelevant      0
79864    80015  query_121  doc_14231     Partial      5
105325  105477  query_199  doc_23741     Partial      5
30934    31013  query_245  doc_13508     Partial      5
101047  101199  query_162  doc_14012     Partial      5

## Make evaluation metrics

In [9]:
from ranx import Qrels

qrels = Qrels.from_df(
    labels_df.astype({"query_id": "str", "product_id": "str"}),
    q_id_col="query_id",
    doc_id_col="product_id", 
    score_col="score",
)

## Encode queries

In [14]:
queries_df["query_embedding"] = model.encode(
    queries_df["query"].tolist()
).tolist()
queries_df.sample(n=5)


query         query_class  \
query_id                                                    
9               coffee table fire pit  Outdoor Fireplaces   
470                   elephant framed            Wall Art   
125                    boho bed frame          Bed Frames   
254          comfortable accent chair       Accent Chairs   
404       large cushion outdoor chair  Furniture Cushions   

                                            query_embedding  
query_id                                                     
9         [0.03264717757701874, 0.09212487190961838, -0....  
470       [-0.006632511503994465, 0.12186688929796219, 0...  
125       [-0.004755771718919277, 0.06739542633295059, -...  
254       [0.05617085099220276, -0.06352565437555313, -0...  
404       [0.03604881465435028, 0.038939010351896286, 0....

In [15]:
queries_df

query  \
query_id                                                      
0                                               salon chair   
1                                        smart coffee table   
2                                                  dinosaur   
3                                         turquoise pillows   
4                                 chair and a half recliner   
...                                                     ...   
483                                             rustic twig   
484       nespresso vertuo next premium by breville with...   
485                                          pedistole sink   
486                                     54 in bench cushion   
487                                              rack glass   

                       query_class  \
query_id                             
0                   Massage Chairs   
1         Coffee & Cocktail Tables   
2                  Kids Wall Décor   
3                   Accent Pillows   
4                        Recliners   
...                            ...   
483          Faux Plants and Trees   
484              Espresso Machines   
485                  Kitchen Sinks   
486             Furniture Cushions   
487                 Candle Holders   

                                            query_embedding  
query_id                                                     
0         [0.00649732630699873, 0.03414246067404747, -0....  
1         [-0.006354459561407566, 0.003995737060904503, ...  
2         [-0.102728933095932, 0.07174915820360184, -0.0...  
3         [-0.0037551824934780598, 0.016025301069021225,...  
4         [0.032879538834095, 0.007315304130315781, 0.02...  
...                                                     ...  
483       [-0.04675285890698433, 0.05521365627646446, 0....  
484       [-0.04700927808880806, 0.02976852096617222, -0...  
485       [0.01754538156092167, 0.023913109675049782, 0....  
486       [0.03463146463036537, 0.04048250988125801, -0....  
487       [0.026542620733380318, 0.06789357960224152, -0...  

[480 rows x 3 columns]

## Search by product name

In [ ]:
from collections import defaultdict

name_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        with_vectors=False,
        with_payload=False,
        limit=100,
    )

    for point in results:
        document_id = f"doc_{point.id}"
        name_run_dict[query_id][document_id] = point.score  
    
name_run_dict

## Create Run object

In [17]:
from ranx import Run

product_name_run = Run(name_run_dict, name="product_name")


## Search by product description

In [18]:
description_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_description", 
            vector=row["query_embedding"]
        ),
        with_vectors=False,
        with_payload=False,
        limit=100,
    )

    for point in results:
        document_id = f"doc_{point.id}"
        description_run_dict[query_id][document_id] = point.score 

product_description_run = Run(
    description_run_dict, 
    name="product_description"
)


## Compare metrics

In [19]:
from ranx import compare

compare(
    qrels=qrels,
    runs=[
        product_name_run, 
        product_description_run
    ],
    metrics=[
        "precision@10", 
        "recall@10", 
        "mrr@10",
        "dcg@10", 
        "ndcg@10",
    ],
)

#    Model                P@10    Recall@10    MRR@10    DCG@10    NDCG@10
---  -------------------  ------  -----------  --------  --------  ---------
a    product_name         0.616ᵇ  0.034ᵇ       0.807ᵇ    19.133ᵇ   0.517ᵇ
b    product_description  0.457   0.024        0.688     14.498    0.388

# Optimizing HNSW search

In [ ]:
from qdrant_client import QdrantClient, models

client = QdrantClient("http://localhost:6333", timeout=600)
client.delete_collection("wands-products")
client.recover_snapshot(
    "wands-products", 
    "https://storage.googleapis.com/deeplearning-course-c1/snapshots/wands-products.snapshot",
)
collection = client.get_collection("wands-products")
collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

In [ ]:
collection.config.hnsw_config

HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None)

In [ ]:
from sentence_transformers import SentenceTransformer
import pandas as pd

model = SentenceTransformer("all-MiniLM-L6-v2")

queries_df = pd.read_csv("query.csv", sep="\t", index_col="query_id")
queries_df["query_embedding"] = model.encode(queries_df["query"].tolist()).tolist()
queries_df.sample(n=5)

/opt/homebrew/Caskroom/miniconda/base/envs/llm/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange


query            query_class  \
query_id                                                    
417                 twin bed frame             Bed Frames   
482           48 inch kitchen hood            Range Hoods   
348                  one alium way                  Sofas   
254       comfortable accent chair          Accent Chairs   
123                 entrance table  Sofa & Console Tables   

                                            query_embedding  
query_id                                                     
417       [0.016311701387166977, 0.03898681327700615, -0...  
482       [0.02213483303785324, 0.13054317235946655, -0....  
348       [0.035170722752809525, -0.0033858150709420443,...  
254       [0.05617085099220276, -0.06352565437555313, -0...  
123       [0.06024651601910591, 0.015183989889919758, -0...

## ANN search

In [ ]:
query = queries_df.iloc[0]["query"]

client.search("wands-products", query_vector=models.NamedVector(
    name="product_name",
    vector=model.encode(query)
),
    limit=3,
    with_vectors=False,
    with_payload=False,
)


[ScoredPoint(id=7465, version=116, score=0.9198918, payload=None, vector=None, shard_key=None, order_value=None),
 ScoredPoint(id=9234, version=144, score=0.8231317, payload=None, vector=None, shard_key=None, order_value=None),
 ScoredPoint(id=42329, version=661, score=0.81807446, payload=None, vector=None, shard_key=None, order_value=None)]

## KNN search

In [ ]:
client.search(
    "wands-products",
    query_vector=models.NamedVector(
        name="product_name",
        vector=model.encode(query)
    ),
    limit=3,
    with_vectors=False,
    with_payload=False,
    search_params=models.SearchParams(exact=True),
)

[ScoredPoint(id=7465, version=116, score=0.9198918, payload=None, vector=None, shard_key=None, order_value=None),
 ScoredPoint(id=9234, version=144, score=0.8231317, payload=None, vector=None, shard_key=None, order_value=None),
 ScoredPoint(id=42329, version=661, score=0.81807446, payload=None, vector=None, shard_key=None, order_value=None)]

## Ground truth

In [ ]:
from collections import defaultdict
from ranx import Qrels

knn_qrels_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"

    results = client.search(
        collection_name='wands-products',
        query_vector=models.NamedVector(
            name="product_name",
            vector=row['query_embedding']
        ),
        limit=100,
        with_vectors=False,
        with_payload=False,
        search_params=models.SearchParams(exact=True),
    )

    for point in results:
        document_id = f"doc_{point.id}"
        knn_qrels_dict[query_id][document_id] = 1

qrels = Qrels.from_dict(knn_qrels_dict)
qrels

DictType[unicode_type,DictType[[unichr x 9],int64]<iv=None>]<iv=None>({query_0: {doc_42446: 1, doc_209: 1, doc_6170: 1, doc_18304: 1, doc_746: 1, doc_16118: 1, doc_4444: 1, doc_18589: 1, doc_33691: 1, doc_12407: 1, doc_22562: 1, doc_11655: 1, doc_42808: 1, doc_1616: 1, doc_29750: 1, doc_19365: 1, doc_10976: 1, doc_6888: 1, doc_5450: 1, doc_16301: 1, doc_20026: 1, doc_40997: 1, doc_27443: 1, doc_19004: 1, doc_42929: 1, doc_18504: 1, doc_14392: 1, doc_1059: 1, doc_31397: 1, doc_14794: 1, doc_24466: 1, doc_8593: 1, doc_25132: 1, doc_26833: 1, doc_1148: 1, doc_42432: 1, doc_42447: 1, doc_37814: 1, doc_2638: 1, doc_34494: 1, doc_23778: 1, doc_15306: 1, doc_25430: 1, doc_38900: 1, doc_32666: 1, doc_42928: 1, doc_32403: 1, doc_22578: 1, doc_33021: 1, doc_24007: 1, doc_26070: 1, doc_4410: 1, doc_31556: 1, doc_42330: 1, doc_26069: 1, doc_24009: 1, doc_18270: 1, doc_24008: 1, doc_18275: 1, doc_18274: 1, doc_24006: 1, doc_40996: 1, doc_19456: 1, doc_18277: 1, doc_36910: 1, doc_18272: 1, doc_25431

In [ ]:
qrels['query_0']


In [ ]:
from ranx import Run

run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    results = client.search(
        collection_name='wands-products',
        query_vector=models.NamedVector(
            name="product_name",
            vector=row['query_embedding']
        ),
        limit=100,
        with_vectors=False,
        with_payload=False,
        search_params=models.SearchParams(exact=False),
    )

    for point in results:
        document_id = f"doc_{point.id}"
        run_dict[query_id][document_id] = point.score

initial_run = Run(run_dict, name="initial_run")
initial_run


DictType[unicode_type,DictType[[unichr x 9],float64]<iv=None>]<iv=None>({query_0: {doc_7465: 0.9198917, doc_9234: 0.8231317, doc_42329: 0.8180744, doc_24010: 0.8144921, doc_18273: 0.8132366, doc_18276: 0.8011743, doc_25431: 0.8008761, doc_18272: 0.78913945, doc_36910: 0.7886271, doc_18277: 0.7806531, doc_19456: 0.7738903, doc_40996: 0.7677348, doc_24006: 0.76630574, doc_18274: 0.7597258, doc_18275: 0.7578185, doc_24008: 0.75755465, doc_18270: 0.75735724, doc_24009: 0.7567274, doc_26069: 0.7553594, doc_42330: 0.75521606, doc_31556: 0.752135, doc_4410: 0.7512181, doc_26070: 0.74578416, doc_4034: 0.74417406, doc_6168: 0.74088377, doc_7506: 0.7403455, doc_28058: 0.73971134, doc_18271: 0.73955727, doc_26068: 0.7357248, doc_15612: 0.73242223, doc_18158: 0.73242223, doc_12409: 0.7313612, doc_6982: 0.7313612, doc_28687: 0.7313612, doc_33689: 0.7294609, doc_39461: 0.72925216, doc_251: 0.7269763, doc_2187: 0.72043693, doc_33690: 0.71746695, doc_31557: 0.71540344, doc_26071: 0.71411836, doc_31555

In [ ]:
from ranx import evaluate

evaluate(
    qrels=qrels,
    run=initial_run,
    metrics=["precision@10", "recall@10", "mrr@10", "dcg@10", "ndcg@10"],
)

{'precision@10': 0.9979166666666667,
 'recall@10': 0.09979166666666668,
 'mrr@10': 0.9979166666666667,
 'dcg@10': 4.534093589467328,
 'ndcg@10': 0.9979166666666667}

## Tweaking HNSW parameters

In [ ]:
client.update_collection(
    collection_name="wands-products",
    hnsw_config=models.HnswConfigDiff(
        m=64,
        ef_construct=200,
    ),
)

True

In [ ]:
import time

time.sleep(1)
collection = client.get_collection("wands-products")
while collection.status != models.CollectionStatus.GREEN:
    time.sleep(1)
    collection = client.get_collection("wands-products")

collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=64, ef_construct=200, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

In [ ]:
tweaked_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        with_vectors=False,
        with_payload=False,
        limit=100,
        search_params=models.SearchParams(
            exact=False,  # disable exact search
        ),
    )
    
    for point in results:
        document_id = f"doc_{point.id}"
        tweaked_run_dict[query_id][document_id] = point.score
    
tweaked_run = Run(
    tweaked_run_dict, 
    name="tweaked"
)
tweaked_run

DictType[unicode_type,DictType[[unichr x 9],float64]<iv=None>]<iv=None>({query_0: {doc_7465: 0.9198917, doc_9234: 0.8231317, doc_42329: 0.8180744, doc_24010: 0.8144921, doc_18273: 0.8132366, doc_18276: 0.8011743, doc_25431: 0.8008761, doc_18272: 0.78913945, doc_36910: 0.7886271, doc_18277: 0.7806531, doc_19456: 0.7738903, doc_40996: 0.7677348, doc_24006: 0.76630574, doc_18274: 0.7597258, doc_18275: 0.7578185, doc_24008: 0.75755465, doc_18270: 0.75735724, doc_24009: 0.7567274, doc_26069: 0.7553594, doc_42330: 0.75521606, doc_31556: 0.752135, doc_4410: 0.7512181, doc_26070: 0.74578416, doc_4034: 0.74417406, doc_6168: 0.74088377, doc_7506: 0.7403455, doc_28058: 0.73971134, doc_18271: 0.73955727, doc_26068: 0.7357248, doc_15612: 0.73242223, doc_18158: 0.73242223, doc_6982: 0.7313612, doc_28687: 0.7313612, doc_12409: 0.7313612, doc_33689: 0.7294609, doc_39461: 0.72925216, doc_251: 0.7269763, doc_2187: 0.72043693, doc_33690: 0.71746695, doc_31557: 0.71540344, doc_26071: 0.71411836, doc_31555

In [ ]:
evaluate(
    qrels=qrels, 
    run=tweaked_run, 
    metrics=["precision@25", "recall@25", "mrr@25", "dcg@25", "ndcg@25"],
)

{'precision@25': 1.0,
 'recall@25': 0.25,
 'mrr@25': 1.0,
 'dcg@25': 8.131765560174184,
 'ndcg@25': 1.0}

# Vector quantization

In [ ]:

client = QdrantClient("http://localhost:6333", timeout=600)
client.delete_collection("wands-products")
client.recover_snapshot(
    "wands-products", 
    "https://storage.googleapis.com/deeplearning-course-c1/snapshots/wands-products.snapshot",
)
collection = client.get_collection("wands-products")
collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

In [ ]:
from sentence_transformers import SentenceTransformer

model = SentenceTransformer("all-MiniLM-L6-v2")

import pandas as pd

queries_df = pd.read_csv(
    "query.csv", 
    sep="\t", 
    index_col="query_id",
)
queries_df["query_embedding"] = model.encode(
    queries_df["query"].tolist()
).tolist()
queries_df.sample(n=5)

query          query_class  \
query_id                                                     
411                     outdoor clock  Weather Instruments   
296           zakariyah twin platform            Kids Beds   
387            self enclosed planters             Planters   
50        tufted chair with gold legs        Accent Chairs   
277               barstool patio sets     Patio Bar Stools   

                                            query_embedding  
query_id                                                     
411       [-0.011927435174584389, 0.08577830344438553, 0...  
296       [-0.053540583699941635, -0.020982783287763596,...  
387       [-0.06903362274169922, 0.036015670746564865, -...  
50        [-0.01810630038380623, 0.0256671030074358, -0....  
277       [0.028116580098867416, 0.02057209052145481, -0...

In [ ]:
from collections import defaultdict
from ranx import Qrels

knn_qrels_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
        search_params=models.SearchParams(
            exact=True,  # enable exact search
        ),
    )
    
    for point in results:
        document_id = f"doc_{point.id}"
        # The conversion to integer is required because ranx expects integers
        knn_qrels_dict[query_id][document_id] = int(point.score * 100)

qrels = Qrels(knn_qrels_dict)
qrels

DictType[unicode_type,DictType[[unichr x 9],int64]<iv=None>]<iv=None>({query_0: {doc_7465: 91, doc_9234: 82, doc_42329: 81, doc_24010: 81, doc_18273: 81, doc_18276: 80, doc_25431: 80, doc_18272: 78, doc_36910: 78, doc_18277: 78, doc_19456: 77, doc_24006: 76, doc_40996: 76, doc_18274: 75, doc_18275: 75, doc_24008: 75, doc_18270: 75, doc_24009: 75, doc_26069: 75, doc_42330: 75, doc_31556: 75, doc_4410: 75, doc_7506: 74, doc_6168: 74, doc_4034: 74, doc_26070: 74, doc_28058: 73, doc_18271: 73, doc_26068: 73, doc_18158: 73, doc_15612: 73, doc_6982: 73, doc_28687: 73, doc_12409: 73, doc_2187: 72, doc_251: 72, doc_33689: 72, doc_39461: 72, doc_33690: 71, doc_31557: 71, doc_26071: 71, doc_31555: 70, doc_6167: 70, doc_39429: 70, doc_39428: 69, doc_9207: 69, doc_8994: 69, doc_975: 69, doc_24007: 68, doc_28059: 68}, query_1: {doc_33698: 83, doc_22679: 81, doc_5173: 81, doc_33290: 81, doc_608: 81, doc_20513: 81, doc_40418: 77, doc_5205: 77, doc_5132: 76, doc_26951: 76, doc_607: 76, doc_35905: 76, 

## Product quantization

In [ ]:
client.update_collection(
    "wands-products",
    quantization_config=models.ProductQuantization(
        product=models.ProductQuantizationConfig(
            compression=models.CompressionRatio.X64,
            always_ram=True,
        )    
    ),
)

True

In [ ]:
import time
time.sleep(1)
collection = client.get_collection("wands-products")
while collection.status != models.CollectionStatus.GREEN:
    time.sleep(1)
    collection = client.get_collection("wands-products")
collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

### without Rescoring

In [ ]:
import numpy as np

response_time = []
pq_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"

    start_time = time.monotonic()

    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name",
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(rescore=False)
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )

    response_time.append(time.monotonic() - start_time)

    for point in results:
        document_id = f"doc_{point.id}"
        pq_run_dict[query_id][document_id] = point.score

np.mean(response_time)


0.0017715488037993055

In [ ]:
from ranx import Run, evaluate

product_name_pq_run = Run(pq_run_dict, name="product_name_pq")

evaluate(
    qrels=qrels,
    run=product_name_pq_run,
    metrics=["precision@25", "recall@25", "mrr@25", "dcg@25", "ndcg@25"],
)

{'precision@25': 0.6402500000000001,
 'recall@25': 0.32012500000000005,
 'mrr@25': 0.913299512987013,
 'dcg@25': 381.49755498423684,
 'ndcg@25': 0.6722111765415885}

### with Rescoring

In [ ]:
import numpy as np

response_time = []
pq_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"

    start_time = time.monotonic()

    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name",
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(rescore=True)
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )

    response_time.append(time.monotonic() - start_time)

    for point in results:
        document_id = f"doc_{point.id}"
        pq_run_dict[query_id][document_id] = point.score

np.mean(response_time)


0.0016832475540013547

In [ ]:
from ranx import Run, evaluate

product_name_pq_rescore_run = Run(pq_run_dict, name="product_name_pq_rescore")

evaluate(
    qrels=qrels,
    run=product_name_pq_rescore_run,
    metrics=["precision@25", "recall@25", "mrr@25", "dcg@25", "ndcg@25"],
)

{'precision@25': 0.8305833333333333,
 'recall@25': 0.41529166666666667,
 'mrr@25': 0.9875,
 'dcg@25': 483.3172810124482,
 'ndcg@25': 0.8603300754404931}

## Scalar quantization

In [ ]:
client.update_collection(
    "wands-products",
    quantization_config=models.ScalarQuantization(
        scalar=models.ScalarQuantizationConfig(
            type=models.ScalarType.INT8,
            always_ram=True,
        )    
    ),
)

True

In [ ]:
time.sleep(1.0)
collection = client.get_collection("wands-products")
while collection.status != models.CollectionStatus.GREEN:
    time.sleep(1.0)
    collection = client.get_collection("wands-products")
    
collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

In [ ]:
response_times = []
sq_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    start_time = time.monotonic()
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(
                rescore=False # Disable re-scoring using the original vectors
            )
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )
    
    response_times.append(time.monotonic() - start_time)
    
    for point in results:
        document_id = f"doc_{point.id}"
        sq_run_dict[query_id][document_id] = point.score
    
np.mean(response_times)

0.001813228281192399

In [ ]:
product_name_sq_run = Run(
    sq_run_dict, 
    name="product_name_sq"
)
evaluate(
    qrels=qrels, 
    run=product_name_sq_run, 
    metrics=["precision@25"]
)

0.9951666666666666

In [ ]:
response_times = []
sq_rescore_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    start_time = time.monotonic()
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(
                rescore=True # Enable re-scoring using the original vectors
            )
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )
    
    response_times.append(time.monotonic() - start_time)
    
    for point in results:
        document_id = f"doc_{point.id}"
        sq_rescore_run_dict[query_id][document_id] = point.score
    
np.mean(response_times)

0.0015865108375540634

In [ ]:
product_name_sq_rescore_run = Run(
    sq_rescore_run_dict, 
    name="product_name_sq_rescore"
)
evaluate(
    qrels=qrels, 
    run=product_name_sq_rescore_run, 
    metrics=["precision@25"]
)

0.9952500000000001

## Binary quantization

In [ ]:
client.update_collection(
    "wands-products",
    quantization_config=models.BinaryQuantization(
        binary=models.BinaryQuantizationConfig(
            always_ram=True,
        )    
    ),
)

True

In [ ]:
time.sleep(1.0)
collection = client.get_collection("wands-products")
while collection.status != models.CollectionStatus.GREEN:
    time.sleep(1.0)
    collection = client.get_collection("wands-products")
    
collection

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=None, indexed_vectors_count=85988, points_count=42994, segments_count=2, config=CollectionConfig(params=CollectionParams(vectors={'product_description': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), 'product_name': VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None)}, shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segm

In [ ]:
response_times = []
bq_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    start_time = time.monotonic()
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(
                rescore=False # Disable re-scoring using the original vectors
            )
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )
    
    response_times.append(time.monotonic() - start_time)
    
    for point in results:
        document_id = f"doc_{point.id}"
        bq_run_dict[query_id][document_id] = point.score
    
np.mean(response_times)

0.0014957432956786457

In [ ]:
product_name_bq_run = Run(
    bq_run_dict, 
    name="product_name_bq"
)
evaluate(
    qrels=qrels, 
    run=product_name_bq_run, 
    metrics=["precision@25"]
)

0.7831666666666666

In [ ]:
response_times = []
bq_rescore_run_dict = defaultdict(dict)
for id, row in queries_df.iterrows():
    query_id = f"query_{id}"
    
    start_time = time.monotonic()
    
    results = client.search(
        collection_name="wands-products",
        query_vector=models.NamedVector(
            name="product_name", 
            vector=row["query_embedding"]
        ),
        search_params=models.SearchParams(
            quantization=models.QuantizationSearchParams(
                rescore=True # Enable re-scoring using the original vectors
            )
        ),
        with_vectors=False,
        with_payload=False,
        limit=50,
    )
    
    response_times.append(time.monotonic() - start_time)
    
    for point in results:
        document_id = f"doc_{point.id}"
        bq_rescore_run_dict[query_id][document_id] = point.score
    
np.mean(response_times)

0.0016467006126883157

In [ ]:
product_name_bq_rescore_run = Run(
    bq_rescore_run_dict, 
    name="product_name_bq_rescore"
)
evaluate(
    qrels=qrels, 
    run=product_name_bq_rescore_run, 
    metrics=["precision@25"]
)

0.9501666666666666

In [ ]:
from ranx import compare

compare(
    qrels=qrels,
    runs=[
        product_name_pq_run, 
        product_name_pq_rescore_run, 
        product_name_sq_run, 
        product_name_sq_rescore_run, 
        product_name_bq_run, 
        product_name_bq_rescore_run,
    ],
    metrics=["precision@25"],
)

#    Model                    P@25
---  -----------------------  ---------
a    product_name_pq          0.640
b    product_name_pq_rescore  0.831ᵃᵉ
c    product_name_sq          0.995ᵃᵇᵉᶠ
d    product_name_sq_rescore  0.995ᵃᵇᵉᶠ
e    product_name_bq          0.783ᵃ
f    product_name_bq_rescore  0.950ᵃᵇᵉ